In [1]:
%matplotlib tk
import matplotlib.pyplot as plt
import cvxpy
import math
import numpy as np
#import cubic_spline_planner

N_IND_SEARCH = 10  # Search index number
show_animation = True

In [2]:
!rm -f Data_Processor.pyc

In [3]:
import numpy as np
import math
from copy import copy, deepcopy
TARGET_SPEED = 20# / 3.6  # [m/s] target speed
MAX_TIME=1500
T=5
NX=4
NU=2
DT=0.2
WB=50
MAX_STEER = np.deg2rad(45.0)  # maximum steering angle [rad]
MAX_DSTEER = np.deg2rad(30.0)  # maximum steering speed [rad/s]
MAX_SPEED = 25#55.0 / 3.6  # maximum speed [m/s]
MIN_SPEED = -25#-20.0 / 3.6  # minimum speed [m/s]
MAX_ACCEL = 5.0  # maximum accel [m/ss]
    


In [4]:
from Motion import Motion,State, get_linear_model_matrix


def np_quad_form(a,b):
        res=a @ b @ a.T
        return res
    
def calc_cost( x, u,xref,t,_B):
        
        R = np.diag([10.0, 10.0])  # input cost matrix
        Rd = np.diag([0.01, 1.0])  # input difference cost matrix
        Q = np.diag([1.0, 1.0, 0.5, 0.5])  # state cost matrix
        Qf = Q  # state final matrix
        

        #cost += cvxpy.quad_form(u[:, t], R)
        #print(u,R)
        l = np_quad_form(u, R) + np_quad_form(xref - x, Q)
        
        
        
        l_x1=2*Q[0,0]*(xref[0]-x[0])*(-1)
        l_x2=2*Q[1,1]*(xref[1]-x[1])*(-1)
        l_x3=2*Q[2,2]*(xref[2]-x[2])*(-1)
        l_x4=2*Q[3,3]*(xref[3]-x[3])*(-1)
            
        l_x=np.array([l_x1,l_x2,l_x3,l_x4])
        l_xx=2 * Q
        Qdiag=np.array([Q[0,0], Q[1,1], Q[2,2], Q[3,3]],dtype=np.float64)
        error=np.array(xref-x)
        #x=Ax+Bu+C
        #dx/du=d(B*u)=B
        l_u1 = 2. * u[0] * R[0,0] #+ np.sum(2*Qdiag*error*(-1)*_B[:,0])
        l_u2 = 2. * u[1] * R[1,1] #+ np.sum(2*Qdiag*error*(-1)*_B[:,1])
        
        l_u = np.array([l_u1, l_u2])

        l_uu = 2. * R
        
        l_ux = np.zeros((NU, NX))

        return l, l_x, l_xx, l_u, l_uu, l_ux
    
def sim_n_steps(_x0,U,xref,N):
    _U=U.copy()
    X=np.zeros((NX,N+1),dtype=np.float64)
    X[:,0]=_x0
    _MS=Motion(DT=DT,WB=WB)
    total_grad=0
    for t in range(N):
        _state=State(x=X[0,t],y=X[1,t],v=X[2,t],yaw=X[3,t])
        _MS.set_state(_state)
        nst,Const=_MS._get_next_state(_U[0,t],_U[1,t])
        B=Const[1]
        x_t1=[nst.x,nst.y,nst.v,nst.yaw]
        u_t=_U[:,t]
        xref_t=xref[:,t]
        cc=calc_cost(x_t1,u_t,xref_t,t,B)
        du=0.2*cc[3]
        #if t <T-1 : U[:,t+1]-=du
        X[:,t+1]=x_t1.copy()
        total_grad+=du
    
    return X,cc,U
def sim_1_step(_X,_U):
    _MS=Motion(DT=DT,WB=WB)
     
    _state=State(x=_X[0],y=_X[1],v=_X[2],yaw=_X[3])
    _MS.set_state(_state)
    nst,Const=_MS._get_next_state(_U[0],_U[1])
    x_t1=[nst.x,nst.y,nst.v,nst.yaw]
  
    return np.array(x_t1,dtype=np.float64)

In [5]:




class iLQRController():
    def __init__(self):
        self.STATE_SIZE=NX
        self.INPUT_SIZE=NU
        self.max_iter=10
        self.dt=0.2
        self.lamb_factor=1.0
        self.lamb_max=10e4
        self.tN=T
        self.eps_converge=0.001
    def ilqr(self, x0, U,xref): 
        #U = np.zeros((NX,T),dtype=np.float64) if U is None else U
        lamb = 1.0 # regularization parameter
        sim_new_trajectory = True
        tN = U.shape[0] # number of time steps
        
        for ii in range(self.max_iter):

            if sim_new_trajectory == True: 
                # simulate forward using the current control trajectory
                X, cost, _ = sim_n_steps(x0, U,xref,T)
                oldcost = copy(cost) # copy for exit condition check

                # 
                f_x = np.zeros((self.tN, self.STATE_SIZE, self.STATE_SIZE)) # df / dx
                f_u = np.zeros((self.tN, self.STATE_SIZE, self.INPUT_SIZE)) # df / du
                # for storing quadratized cost function 

                l = np.zeros((self.tN,1)) # immediate state cost 
                l_x = np.zeros((self.tN, self.STATE_SIZE)) # dl / dx
                l_xx = np.zeros((self.tN, self.STATE_SIZE, self.STATE_SIZE)) # d^2 l / dx^2
                l_u = np.zeros((self.tN, self.INPUT_SIZE)) # dl / du
                l_uu = np.zeros((self.tN, self.INPUT_SIZE, self.INPUT_SIZE)) # d^2 l / du^2
                l_ux = np.zeros((self.tN, self.INPUT_SIZE, self.STATE_SIZE)) # d^2 l / du / dx
                # for everything except final state
                for t in range(self.tN):
                    # x(t+1) = f(x(t), u(t)) = x(t) + dx(t) * dt
                    # linearized dx(t) = np.dot(A(t), x(t)) + np.dot(B(t), u(t))
                    # f_x = (np.eye + A(t)) * dt
                    # f_u = (B(t)) * dt
                    # continuous --> discrete
                    A, B, C = get_linear_model_matrix(X[2,t],X[3,t], U[1,t])
                    f_x[t] = A
                    f_u[t] = B 

                    
                    (l[t], l_x[t], l_xx[t], l_u[t], l_uu[t], l_ux[t]) = calc_cost(X[:,t], U[:,t],xref[:,t],t,B)
                    

                # and for final state
                #l[-1], l_x[-1], l_xx[-1] = self.cost_final(X[-1])

                sim_new_trajectory = False

            V = l[-1].copy() # value function
            V_x = l_x[-1].copy() # dV / dx
            V_xx = l_xx[-1].copy() # d^2 V / dx^2
            k = np.zeros((self.tN, self.INPUT_SIZE)) # feedforward modification
            K = np.zeros((self.tN, self.INPUT_SIZE, self.STATE_SIZE)) # feedback gain

            # work backwards to solve for V, Q, k, and K
            for t in range(self.tN-2, -1, -1):
                
                Q_x = l_x[t] + np.dot(f_x[t].T, V_x) 
                Q_u = l_u[t] + np.dot(f_u[t].T, V_x)

                Q_xx = l_xx[t] + np.dot(f_x[t].T, np.dot(V_xx, f_x[t])) 
                Q_ux = l_ux[t] + np.dot(f_u[t].T, np.dot(V_xx, f_x[t]))
                Q_uu = l_uu[t] + np.dot(f_u[t].T, np.dot(V_xx, f_u[t]))

                Q_uu_evals, Q_uu_evecs = np.linalg.eig(Q_uu)
                Q_uu_evals[Q_uu_evals < 0] = 0.0
                #Q_uu_evals += lamb
                Q_uu_inv = np.dot(Q_uu_evecs, np.dot(np.diag(1.0/Q_uu_evals), Q_uu_evecs.T))
                #k[t]=-1*l_u[t]
                k[t] = -1. * np.dot(Q_uu_inv, Q_u)
                K[t] = -1. * np.dot(Q_uu_inv, Q_ux)

                V_x = Q_x - np.dot(K[t].T, np.dot(Q_uu, k[t]))
                V_xx = Q_xx - np.dot(K[t].T, np.dot(Q_uu, K[t]))

            U_new = np.zeros((NU,T),dtype=np.float64)
            x_new = np.zeros((NX,T),dtype=np.float64)
            x_new = x0.copy()
            for t in range(self.tN - 1): 
                # use feedforward (k) and feedback (K) gain matrices 
                # calculated from our value function approximation
                U_new[:,t] = U[:,t] + k[t] + np.dot(K[t], x_new - X[:,t])
                x_new_1= sim_1_step(x_new, U_new[:,t])
                x_new=x_new_1.copy()
            # evaluate the new trajectory 
            X_new, cost_new , _= sim_n_steps(x0, U_new,xref,T)
            #if 1==1:
            if cost_new[0] < cost[0]: 
                # decrease lambda (get closer to Newton's method)
                lamb /= self.lamb_factor

                X = copy(X_new) # update trajectory 
                U = copy(U_new) # update control signal
                oldcost = copy(cost)
                cost = copy(cost_new)

                sim_new_trajectory = True # do another rollout

                # check to see if update is small enough to exit
                print('...',cost[0],oldcost[0])
                if ii > 0 and ((abs(oldcost[0]-cost[0])/cost[0]) < self.eps_converge):
                    #print("Converged at iteration = %d; Cost = %.4f;"%(ii,cost_new) + 
                    #        " logLambda = %.1f"%np.log(lamb))
                    print("break 1",ii)
                    break

            else: 
                # increase lambda (get closer to gradient descent)
                lamb *= self.lamb_factor
                # print("cost: %.4f, increasing lambda to %.4f")%(cost, lamb)
                if lamb > self.lamb_max: 
                    #print("lambda > max_lambda at iteration = %d;"%ii + 
                    #    " Cost = %.4f; logLambda = %.1f"%(cost, np.log(lamb)))
                    print("break 2",ii)
                    break

        return X, U, cost
    

In [6]:
from Car_Env import Car_Env
from Data_Processor import Data_Processor
from Car_Plot import Move_Contour,Draw_Car

In [7]:
#cx, cy, cyaw, ck = get_switch_back_course(dl)
dl=1.0
rec=True
max_len=350
qlen=35
car_move=True

Env=Car_Env(rec=rec,max_len=max_len,qlen=qlen,rec_path="Rec_iLQR")
[init_state,map_points]=Env.reset()
mpx=np.array(map_points[:max_len,0])#-ofx
mpy=np.array(map_points[:max_len,1])#-ofy
ix,iy,iyaw,ivel=init_state[0]
_traj=init_state[1][0]
_dind=init_state[1][1]
_end=init_state[1][2]
ofx,ofy,ofang=init_state[2]
img=init_state[3]
state = State(x=ix, y=iy, yaw=iyaw, v=ivel)
#print(init_state)

Track generation: 1234..1551 -> 317-tiles track
retry to generate track (normal if there are not many of this messages)
Track generation: 1225..1535 -> 310-tiles track


In [8]:
if rec==True:
    import os
    if not os.path.exists('Rec_iLQR/'):
        os.mkdir('Rec_iLQR')
    if not os.path.exists('Rec_iLQR_Raw/'):
        os.mkdir('Rec_iLQR_Raw')
    if not os.path.exists('Fig_iLQR/'):
        os.mkdir('Fig_iLQR')


In [9]:
import cv2
import matplotlib.gridspec as gridspec
phi=0
rot_mat=np.array([[math.cos(phi),math.sin(phi)],[-math.sin(phi),math.cos(phi)]])
time = 0.0
x = [state.x]
y = [state.y]
yaw = [state.yaw]
v = [state.v]
t = [0.0]
d = [0.0]
a = [0.0]

log_state=[]
log_traj=[]
log_img=[]
log_act=[]
log_next_state=[]


#index, _ = get_closest_point(state, _cx, _cy, cyaw, 0)
odelta, oa = None, None
_index=0
#cyaw = smooth_yaw(cyaw)
accl,gas,steer=0,0,0
state_str=''
act_str=''
xref_str=''
xbar_str=''


_Data_Processor=Data_Processor(_speed=TARGET_SPEED,tlen=qlen)
acc_st=State(x=0,y=0)
itr=0
#fig,axes=plt.subplots(nrows=2,ncols=1,figsize=(10,10))
fig=plt.figure(figsize=(10,10))
gs = fig.add_gridspec(3, 1)
ax1=fig.add_subplot(gs[0,:])
ax2=fig.add_subplot(gs[1:,:])
axes=[ax1,ax2]


def map_plot(vect,_ofx,_ofy,_ofang):
    _vect=np.array(vect,dtype=np.float64).copy()
    _ofang=-1*_ofang
    rot_mat=np.array([[math.cos(_ofang),math.sin(_ofang)],[-math.sin(_ofang),math.cos(_ofang)]])
    _vect=np.matmul(rot_mat,_vect)

    _vect[0]+=_ofx
    _vect[1]+=_ofy
    return [_vect[0],_vect[1]]
def inv_map_plot(vect,_ofx,_ofy,_ofang):
    _vect=np.array(vect,dtype=np.float64).copy()
    _vect[0]-=_ofx
    _vect[1]-=_ofy
    _ofang=1*_ofang
    rot_mat=np.array([[math.cos(_ofang),math.sin(_ofang)],[-math.sin(_ofang),math.cos(_ofang)]])
    _vect=np.matmul(rot_mat,_vect)
    return [_vect[0],_vect[1]]
U=np.zeros((NU,T),dtype=np.float64)
iLQR=iLQRController()
while MAX_TIME >= time:
      
        _full_state = np.array([state.x, state.y, state.v, state.yaw],dtype=np.float64)
    
        
        _full_state_traj=_Data_Processor.update_trajectory(_traj)
        xref, dref = _Data_Processor.get_ref_trajectory(state,dl,DT,T)
        
        if _end==True:
            break

        _index+=_dind
        
        #oa, odelta, ox, oy, oyaw, ov ,xbar= iterative_linear_mpc_control(xref, Motion_Status, dref, oa, odelta)
        X,U, cost= iLQR.ilqr(_full_state, U, xref )
        oa=U[0,1]
        odelta=U[1,1]
        ox=X[0,1]
        oy=X[1,1]
        ov=X[2,1]
        oyaw=X[3,1]
        state_str=' x: '+str('%0.4f'%state.x)+' y: '+str('%0.4f'%state.y)+' v: '+str('%0.4f'%state.v)+' yaw: '+str('%0.4f'%np.rad2deg(state.yaw))+'\n'
        xref_str =' x: '+str('%0.4f'%xref[0][0])+' y: '+str('%0.4f'%xref[1][0])+' v: '+str('%0.4f'%xref[2][0])+' yaw: '+str('%0.4f'%np.rad2deg(xref[3][0]))+'\n'
        time_str ='Time(Sec): '+str('%0.4f'%time)+' Sec Distance(m): '+str('%0.4f'%_index)+' m '+'\n'
        #xbar_str=str(xbar[0][0])+','+str(xbar[1][0])+','+str(xbar[2][0])+','+str(np.rad2deg(xbar[3][0]))+'\n'
        act_str  =' accel: '+str('%0.4f'%accl)+' gas: '+str('%0.4f'%gas)+' steer: '+str('%0.4f'%np.rad2deg(steer))+'\n'
    
        #xref_str=str(xref[3][0])+'\n'
        #xbar_str=str(xbar[3][:])+'\n'
        max_steer=np.deg2rad(45)
        max_accl=5
        if odelta is not None:
            if abs(U[1,0])<max_steer:
                  di= U[1,0]
            else:
                di=(U[1,0]/abs(U[1,0]))*max_steer
            
            if abs(U[0,0])<max_accl:
                  ai=U[0,0]
            else:
                ai=(U[0,0]/abs(U[0,0]))*max_accl
        accl=ai
        steer=di
        
        #act_str=str(steer)+'\n'
        nst,path,offset,img,rw,ter,info=Env.step([steer,accl,0])
        img_raw=Env.render(mode='rgb_array')
        _traj,_dind,_end=path
        ofx,ofy,ofang=offset
        
        gas=Env.gas
        
        state=State(x=nst[0],y=nst[1],yaw=nst[2],v=nst[3])
        #Motion_Status.set_state(next_state)
        
        log_state.append(_full_state)
        log_traj.append(_full_state_traj)
        log_img.append(img)
        log_act.append([accl,steer,0])
        log_next_state.append(state)
        
        time = time + DT
        if car_move==True:
            _xref=xref.copy()
            [_ox,_oy]=map_plot([ox,oy],ofx,ofy,ofang)
            [_xref[0,:],_xref[1,:]]=map_plot([xref[0,:],xref[1,:]],ofx,ofy,ofang)
            [_x,_y]=map_plot([state.x,state.y],ofx,ofy,ofang)
            car_x,car_y,car_ang=ofx,ofy,ofang
            _mpx,_mpy=mpx,mpy
        else:
            _ox,_oy=ox,oy
            _xref=xref
            _x,_y=state.x,state.y
            car_x,car_y,car_ang=state.x,state.y,state.yaw
            [_mpx,_mpy]=inv_map_plot([mpx,mpy],ofx,ofy,ofang)
        x.append(_x)
        y.append(_y)
        yaw.append(ofang)
        v.append(state.v)
        t.append(time)
        d.append(di)
        a.append(ai)

        
    
      
        
        if show_animation:  # pragma: no cover
            axes[0].cla()
            axes[1].cla()
            axes[0].text(.01,.6,'Running : '+time_str,fontsize=10,color='c')
            axes[0].text(.01,.4,'state : '+state_str,fontsize=10,color='r')
            axes[0].text(.01,.2,'xref : '+xref_str,fontsize=10,color='b')
            axes[0].text(.01,0,'act : '+act_str,fontsize=10,color='g')
            
            if ox is not None:
                axes[1].plot(_ox, _oy, "xr", label="MPC",alpha=1.0)
            axes[1].plot(_mpx, _mpy, "-b", label="course")
            axes[1].plot(x, y, "oc", label="trajectory")
            axes[1].plot(_xref[0, :], _xref[1, :], "xk", label="xref",alpha=1.0)
            axes[1].plot(_mpx[_index], _mpy[_index], "xg", label="target",alpha=1.0)
            #plot_car(state.x, state.y, state.yaw, steer=di)
            
            car_points=Draw_Car(car_x,car_y)
            rp=Move_Contour(car_points,0,0,car_ang)
            r_car_points=rp.apply()
            r_points=np.array(r_car_points,dtype=np.float64)
            axes[1].plot(r_points[:,0].flatten(),r_points[:,1].flatten(),"-r")
            
            plt.axis("equal")
            plt.grid(True)
            #plt.title("Time[s]:" + str(round(time, 2))
            #          + ", speed[km/h]:" + str(round(state.v * 3.6, 2))
            #          + '\nyaw'+str(state.yaw)
            #          + '\nxref_yaw'+str(xref[3][0])
            #          + '\nsteer'+str(steer))
            #fig.canvas.draw()
            plt.pause(0.0001)
            if itr%1==0:
                plt.savefig('Fig_iLQR/'+str(int(itr/1))+'.jpg')
                cv2.imwrite('Rec_iLQR/'+str(int(itr/1))+'.jpg',img)
                cv2.imwrite('Rec_iLQR_Raw/'+str(int(itr/1))+'.jpg',img_raw)
            itr+=1
            if ter==True:
                print('terminal ... ')
                
if show_animation:  # pragma: no cover
            plt.close("all")
            plt.subplots()
            plt.plot(car_x, car_y, "-r", label="spline")
            plt.plot(x, y, "-g", label="tracking")
            plt.grid(True)
            plt.axis("equal")
            plt.xlabel("x[m]")
            plt.ylabel("y[m]")
            plt.legend()

            plt.subplots()
            plt.plot(t, v, "-r", label="speed")
            plt.grid(True)
            plt.xlabel("Time [s]")
            plt.ylabel("Speed [kmh]")

            plt.show()


... 377.9906769241888 395.9996943824171
... 377.99067688741115 377.9906769241888
break 1 1
... 55.40420676488785 56.58306140080508
... 44.11818351489046 44.285968642701064
... 42.06582076159016 44.11818351489046
... 48.48444521719667 50.83596262015564
... 41.67589457624376 41.88397271911706
... 41.10868581057948 42.9600914900225
... 37.343112111160025 37.7116588417037
... 36.4092932695261 37.343112111160025
... 43.34599192429229 46.75827789016755
... 37.146033451267485 37.46069953037405
... 35.785242359840375 37.146033451267485
... 46.47336745315694 47.2540722994747
... 32.39168764773142 32.51366794731944
... 31.952746499375873 32.39168764773142
... 44.55962638966518 45.292923482338
... 27.824521018035238 27.85226446810489
... 27.67208471723079 27.824521018035238
... 34.91111038621755 35.185851435791676
... 23.481358956909553 23.504681393203377
... 23.44126365119138 23.481358956909553
... 29.434166130658678 29.661216641249737
... 28.316020441589615 28.33720251145106
... 25.898014359153

terminal ... 
... 18.022310956440652 18.024644042283906
terminal ... 
... 20.33364354451047 20.338016736838217
... 20.33361843344069 20.33364354451047
break 1 1
terminal ... 
... 22.858728396622055 22.864305162213142
... 22.858685537538122 22.858728396622055
break 1 1
terminal ... 
... 7.314642262228747 7.386681028184252
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
... 12.859791294389257 12.86504282308893
... 12.859430639667732 12.859791294389257
break 1 1
terminal ... 
... 14.619826820875376 14.620425174546678
... 14.619772906920883 14.619826820875376
break 1 1
terminal ... 
... 16.598058315152198 16.600362425154213
... 16.598058232480156 16.598058315152198
break 1 1
terminal ... 
... 18.79076339916876 18.794185168320325
... 18.790761223387673 18.79076339916876
break 1 1
terminal ... 
... 21.199483669414896 21.20430921366054
... 21.199469069856317 21.199483669414896
break 1 1
terminal ... 
... 6.849483137363338 6.920512417873778
terminal ... 
terminal ... 
ter

terminal ... 
... 24.52537798088328 24.533583096855878
... 24.525377946617716 24.52537798088328
break 1 1
terminal ... 
... 6.523715512051578 6.557278534332865
terminal ... 
terminal ... 
terminal ... 
... 10.136386625260116 10.137145992626317
... 10.136386510910247 10.136386625260116
break 1 1
terminal ... 
... 11.799577355266447 11.801118383679292
... 11.799577305177763 11.799577355266447
break 1 1
terminal ... 
... 13.69193938618175 13.694775993829156
... 13.691939378989238 13.69193938618175
break 1 1
terminal ... 
... 15.81286151311172 15.816986865681967
... 15.812861510519602 15.81286151311172
break 1 1
terminal ... 
... 18.162063335377095 18.16747236399871
... 18.16206333449801 18.162063335377095
break 1 1
terminal ... 
... 20.739219861242294 20.74590720936769
... 20.739219856794982 20.739219861242294
break 1 1
terminal ... 
... 23.543918950233042 23.551878652280628
... 23.543918936870377 23.543918950233042
break 1 1
terminal ... 
... 6.162477210149709 6.198436122899641
terminal 

terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
... 16.061687499255807 16.068447198764332
terminal ... 
... 18.56578363399331 18.57207064199346
... 18.56557352926392 18.56578363399331
break 1 1
terminal ... 
... 21.30751140240718 21.328970742861873
... 21.306017850680828 21.30751140240718
break 1 1
terminal ... 
... 24.271767524078772 24.295648132178933
... 24.269316601885592 24.271767524078772
break 1 1
terminal ... 
... 27.464368107716894 27.494888125603456
... 27.460183893594277 27.464368107716894
break 1 1
terminal ... 
... 7.513307531949593 10.665868633942255
terminal ... 
terminal ... 
terminal ... 
terminal ... 
... 14.51222220453727 14.520798195657665
... 14.508962131647113 14.51222220453727
break 1 1
terminal ... 
terminal ... 
... 19.442570401228995 19.486376427144364
... 19.436784489811767 19.442570401228995
break 1 1
terminal ... 
... 22.212680581994693 22.248102589518883
... 22.2060628258632 22.212680581994693
break 1 1
terminal ... 
... 25.1998844917

terminal ... 
... 11.942357972030567 11.999390023000425
terminal ... 
... 14.037372148477724 14.064872010866958
terminal ... 
... 16.35979987169104 16.390929538533815
... 16.359671885180248 16.35979987169104
break 1 1
terminal ... 
... 18.90328404832858 18.93089081210541
... 18.902700695563233 18.90328404832858
break 1 1
terminal ... 
... 21.689912510676464 21.71520351492217
... 21.68899515039778 21.689912510676464
break 1 1
terminal ... 
... 24.708006815026792 24.73095385747845
... 24.706905840652894 24.708006815026792
break 1 1
terminal ... 
... 27.959809492633248 27.98114238184806
... 27.95863767138434 27.959809492633248
break 1 1
terminal ... 
... 7.725067569074879 10.78869990147793
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
... 17.317940459698665 17.353675991047623
... 17.317732343198596 17.317940459698665
break 1 1
terminal ... 
... 19.898963119411363 19.94888378564416
... 19.894834962634153 19.898963119411363
break 1 1
terminal ... 
... 22.698745480090

...

terminal ... 
... 11.844935639469657 16.734040228219907
... 11.832793254720274 11.844935639469657
... 11.831949968417762 11.832793254720274
break 1 2
terminal ... 
... 13.781125550485402 14.045264578867338
... 13.780065790145388 13.781125550485402
break 1 1
terminal ... 
... 15.987750948602994 16.18116970487464
... 15.974046870514762 15.987750948602994
break 1 1
terminal ... 
... 18.33847232962523 18.51862673712748
... 18.31021820549672 18.33847232962523
... 18.304978435741837 18.31021820549672
break 1 2
terminal ... 
... 20.847416920880654 21.019903281850777
... 20.80224882591101 20.847416920880654
... 20.790291437414353 20.80224882591101
break 1 2
terminal ... 
... 23.459204143674718 23.649785432869503
... 23.39484977254645 23.459204143674718
... 23.373053345802596 23.39484977254645
break 1 2
terminal ... 
... 26.421700858102874 26.697670762128794
... 26.31393887411026 26.421700858102874
... 26.269461415782903 26.31393887411026
... 26.250488862697818 26.269461415782903
break 1 3
term

terminal ... 
... 28.084834256642626 28.105351934206087
... 28.08247879370719 28.084834256642626
break 1 1
terminal ... 
... 6.540336788117961 6.601565416707576
... 6.536045407548491 6.540336788117961
break 1 1
terminal ... 
... 7.984904318729945 7.986804644203769
... 7.984711156019311 7.984904318729945
break 1 1
terminal ... 
... 9.66596684759576 9.668030931120077
... 9.66498233757673 9.66596684759576
break 1 1
terminal ... 
... 11.589855072585003 11.593003590689426
... 11.589588814322886 11.589855072585003
break 1 1
terminal ... 
... 13.793845696049027 13.799630573765327
... 13.793788527755611 13.793845696049027
break 1 1
terminal ... 
... 16.232799179639947 16.240399691185253
terminal ... 
... 18.9227427063652 18.932655704639288
... 18.9226603540553 18.9227427063652
break 1 1
terminal ... 
... 21.854792408236676 21.86700533670618
... 21.854440667036467 21.854792408236676
break 1 1
terminal ... 
... 25.029642352448036 25.044502756477314
... 25.028834605452143 25.029642352448036
break

terminal ... 
... 8.806441301485163 9.750146044078884
... 8.797123822375008 8.806441301485163
terminal ... 
... 10.670505325466438 10.714468469393417
terminal ... 
... 12.787012164248639 12.798521467587696
terminal ... 
... 15.074685293559764 15.082678944686897
... 15.074421481990923 15.074685293559764
break 1 1
terminal ... 
... 17.65573078748963 17.67407279796562
... 17.65465988384507 17.65573078748963
break 1 1
terminal ... 
... 20.582645567262688 20.614409154016222
... 20.579126881609668 20.582645567262688
break 1 1
terminal ... 
... 23.76927381064798 23.813813643100406
... 23.76169622804002 23.76927381064798
break 1 1
terminal ... 
... 27.183268974722488 27.242518528981623
... 27.169393315237585 27.183268974722488
break 1 1
terminal ... 
... 30.818126472657504 30.8958737039103
... 30.794901176934008 30.818126472657504
break 1 1
terminal ... 
... 7.818257034243489 8.673992957607485
... 7.801540142854912 7.818257034243489
terminal ... 
... 9.548955014221537 9.572722996498316
termina

terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
... 7.729024642301268 7.780088265157122
... 7.721169667745016 7.729024642301268
terminal ... 
... 9.482233678485521 9.48633037423173
... 9.482024451464891 9.482233678485521
break 1 1
terminal ... 
... 11.469206453434014 11.478267987806877
... 11.469014694478206 11.469206453434014
break 1 1
terminal ... 
... 13.663105192994156 13.67956738922584
... 13.663037670809127 13.663105192994156
break 1 1
terminal ... 
... 16.187891786119355 16.20512312249546
terminal ... 
... 18.979256491162378 18.997917895327994
terminal ... 
... 22.020352462186082 22.03982589741515
... 22.020213941203732 22.020352462186082
break 1 1
terminal ... 
... 25.3160271149036 25.335211282314017
... 25.315634579646822 25.3160271149036
break 1 1
terminal ... 
... 28.861408370121648 28.88113570338208
... 28.86062482818274 28.861408370121648
break 1 1
terminal ... 
... 32

terminal ... 
... 14.177947374954023 14.210080935398366
... 14.177880181975084 14.177947374954023
break 1 1
terminal ... 
... 16.790713343712373 16.837427579010857
terminal ... 
... 19.74439865358641 19.781871884263726
terminal ... 
... 22.985276861423856 23.021667948513905
... 22.984649954443462 22.985276861423856
break 1 1
terminal ... 
... 26.446810729029764 26.47702398563686
... 26.44527724462566 26.446810729029764
break 1 1
terminal ... 
... 30.15681392074499 30.186282323985303
... 30.153898198700876 30.15681392074499
break 1 1
terminal ... 
... 34.094283787230786 34.12531392599611
... 34.08948913387461 34.094283787230786
break 1 1
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
terminal ... 
... 7.24234599357308 7.285543397995775
... 7.235877465275442 7.24234599357308
break 1 1
terminal ... 
... 8.992854825304173 8.997759804578791
... 8.992567010813655 8.992854825304173
break 1 1
terminal ... 
... 10.98

In [10]:
log_dict={
'state':log_state,
'traj':log_traj,
'image':log_img,
'action':log_act,
'next_sate':log_next_state
}

In [11]:
str('%0.2f'%0.0)

'0.00'

In [12]:
import pickle
f=open('dataset_iLQR','wb')
pickle.dump(log_dict,f)
f.close()
itr

3209

In [13]:
f=open('dataset_iLQR','rb')
dataset=pickle.load(f)
f.close()

In [14]:
dataset

{'state': [array([0.00000000e+00, 0.00000000e+00, 1.23695832e-06, 0.00000000e+00]),
  array([0.        , 0.        , 0.00809624, 0.        ]),
  array([0.        , 0.        , 0.01468037, 0.        ]),
  array([0.        , 0.        , 0.02162805, 0.        ]),
  array([0.        , 0.        , 0.02857835, 0.        ]),
  array([0.        , 0.        , 0.03560442, 0.        ]),
  array([0.        , 0.        , 0.04269422, 0.        ]),
  array([0.        , 0.        , 0.04985173, 0.        ]),
  array([0.        , 0.        , 0.05707742, 0.        ]),
  array([0.        , 0.        , 0.06437222, 0.        ]),
  array([0.        , 0.        , 0.07173672, 0.        ]),
  array([0.        , 0.        , 0.07917149, 0.        ]),
  array([0.        , 0.        , 0.08667701, 0.        ]),
  array([0.        , 0.        , 0.09425368, 0.        ]),
  array([0.        , 0.        , 0.10190184, 0.        ]),
  array([0.        , 0.        , 0.10962187, 0.        ]),
  array([0.        , 0.        

In [15]:
np.arctan2(1,1)

0.7853981633974483

In [16]:
#%matplotlib inline
plt.plot(cx,cy)
plt.show()

NameError: name 'cx' is not defined

In [ ]:
plt.plot(range(len(cyaw)),cyaw)
plt.show()

In [ ]:
dcx=np.gradient(cx)
dcy=np.gradient(cy)
cyaw=[np.arctan2(y,x) for x,y in zip(dcx,dcy)]

In [ ]:
cx, cy, cyaw, ck, s = cubic_spline_planner.calc_spline_course(tx,ty,ds=dl)
yaw0=np.deg2rad(90)
cyaw=[yaw-yaw0 for yaw in cyaw]

In [ ]:
import numpy as np
np.rad2deg(2.64)

In [ ]:
cyaw

In [ ]:
import cvxpy as cp
import numpy as np

# Problem data.
m = 1
n = 1
np.random.seed(1)
A = 10#np.random.randn(m, n)
b = 5#np.random.randn(m)

# Construct the problem.
x = cp.Variable(n)
objective = cp.Minimize(cp.sum_squares(A*x - b))
constraints = [0 <= x, x <= 1]
prob = cp.Problem(objective, constraints)

# The optimal objective value is returned by `prob.solve()`.
result = prob.solve()
# The optimal value for x is stored in `x.value`.
print(x.value)
# The optimal Lagrange multiplier for a constraint is stored in
# `constraint.dual_value`.
print(constraints[0].dual_value)

In [ ]:
print(x.value)

In [ ]:
x=np.array(range(0,100))
x=x/100

In [ ]:
y=10*x-5
y=np.square(y)
plt.plot(x,y)
plt.show()

In [ ]:
import gym
gym.make('CarRacing-v0')

In [ ]:
img_raw